In [2]:
import datetime
import warnings
warnings.filterwarnings('ignore')
import torch
from glob import glob
import os
from torch.utils.data import Dataset, DataLoader
import pandas as pd
from tqdm import tqdm
import numpy as np
from torchvision import transforms
import torchvision.models as models
import torch.nn as nn
from torch.nn import functional as F
from sklearn.model_selection import KFold
import time
#from efficientnet_pytorch import EfficientNet
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import train_test_split


import matplotlib.pyplot as plt
#from torch_poly_lr_decay import PolynomialLRDecay
import random
from torchvision import models
from sklearn.metrics import accuracy_score, log_loss
import math
import librosa

os.getcwd()

'/home/clim-lab/바탕화면/main_drive/jiwon/retrieval'

In [3]:
os.environ['CUDA_VISIBLE_DEVICES'] = '0,1'
torch.set_num_threads(8)
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
print(device)

cuda:0


In [4]:
import random
import torchaudio

class RandomClip:
    '''
    transforms.Vad -> attempts to trim silence and quiet background sounds from the ends of recordings of speech.
    '''

    def __init__(self, sample_rate, clip_length):
        self.clip_length = clip_length
        self.vad = torchaudio.transforms.Vad(
            sample_rate=sample_rate, trigger_level=7.0)

    def __call__(self, audio_data):
        audio_length = audio_data.shape[0]
        if audio_length > self.clip_length:
            offset = random.randint(0, int(audio_length-self.clip_length)) #(0,x)사이의 랜덤한 정수 반환
            audio_data = audio_data[offset:(offset+self.clip_length)]

        return self.vad(audio_data) # remove silences at the beggining/end

In [5]:
import os
wav_path = os.listdir('./data/Clotho/waveforms/train/')

In [6]:
import os
wav_path = os.listdir('./data/Clotho/waveforms/train/')

sampling_rate = 32000 
audio_data, sr = torchaudio.load(os.path.join('./data/Clotho/waveforms/train/', wav_path[1]))
clip_transformer = RandomClip(sampling_rate, 64000)  #clip_length=8
clip_audio = clip_transformer(audio_data)              
print(clip_audio)
print(clip_audio.shape)

tensor([[ 0.0216,  0.0216,  0.0199,  ..., -0.0023, -0.0020, -0.0016]])
torch.Size([1, 1115660])


In [7]:
audio_ex1, sr1 = torchaudio.load(os.path.join('./data/Clotho/waveforms/train/', wav_path[1]))
print(audio_ex1)
print(audio_ex1.shape)

audio_ex2, sr2 = librosa.load(os.path.join('./data/Clotho/waveforms/train/', wav_path[1]))
print(audio_ex2)
print(audio_ex2.shape)


tensor([[ 0.0005,  0.0007,  0.0007,  ..., -0.0023, -0.0020, -0.0016]])
torch.Size([1, 1261260])
[ 0.00042238  0.00072047  0.00072089 ... -0.00280746 -0.00228519
 -0.00202156]
(630630,)


In [8]:
audio_ex1.ravel().shape

torch.Size([1261260])

In [9]:
import random

class RandomSpeedChange:
    def __init__(self, sample_rate):
        self.sample_rate = sample_rate

    def __call__(self, audio_data):
        speed_factor = random.choice([0.9, 1.0, 1.1])
        if speed_factor == 1.0: # no change
            return audio_data

        # change speed and resample to original rate:
        sox_effects = [
            ["speed", str(speed_factor)],
            ["rate", str(self.sample_rate)],
        ]
        transformed_audio, _ = torchaudio.sox_effects.apply_effects_tensor(
            audio_data, self.sample_rate, sox_effects)
        return transformed_audio

speed_transform = RandomSpeedChange(sampling_rate)
transformed_audio = speed_transform(audio_data)

In [10]:
print(transformed_audio)
print(transformed_audio.shape)

tensor([[ 0.0005,  0.0007,  0.0007,  ..., -0.0021, -0.0020, -0.0015]])
torch.Size([1, 1401400])


In [11]:
import random
import torchaudio
import math
import os
import pathlib
import torch

class RandomClip:
    def __init__(self, sample_rate, clip_length):
        self.clip_length = clip_length
        #self.sequence_length = sequence_length

        self.vad = torchaudio.transforms.Vad(
            sample_rate=sample_rate, trigger_level=7.0)

    def __call__(self, audio_data):
        audio_length = audio_data.shape[0]
        if audio_length > self.clip_length:
            offset = random.randint(0, audio_length-self.clip_length)
            audio_data = audio_data[offset:(offset+self.clip_length)]

        return self.vad(audio_data) # remove silences at the beggining/end
    


class RandomSpeedChange:
    def __init__(self, sample_rate):
        self.sample_rate = sample_rate

    def __call__(self, audio_data):
        speed_factor = random.choice([0.9, 1.0, 1.1])
        if speed_factor == 1.0: # no change
            return audio_data

        # change speed and resample to original rate:
        sox_effects = [
            ["speed", str(speed_factor)],
            ["rate", str(self.sample_rate)],
        ]
        transformed_audio, _ = torchaudio.sox_effects.apply_effects_tensor(
            audio_data, self.sample_rate, sox_effects)
        return transformed_audio


class RandomBackgroundNoise:
    '''
    pick a random noise file from a given folder and will apply it to the original audio file.
    '''
    def __init__(self, sample_rate, noise_dir, min_snr_db=0, max_snr_db=15):
        self.sample_rate = sample_rate
        self.min_snr_db = min_snr_db
        self.max_snr_db = max_snr_db

        if not os.path.exists(noise_dir):
            raise IOError(f'Noise directory `{noise_dir}` does not exist')
        # find all WAV files including in sub-folders:
        self.noise_files_list = list(pathlib.Path(noise_dir).glob('**/*.wav'))
        if len(self.noise_files_list) == 0:
            raise IOError(f'No .wav file found in the noise directory `{noise_dir}`')

    def __call__(self, audio_data):
        random_noise_file = random.choice(self.noise_files_list)
        effects = [
            ['remix', '1'], # convert to mono
            ['rate', str(self.sample_rate)], # resample
        ]
        noise, _ = torchaudio.sox_effects.apply_effects_file(random_noise_file, effects, normalize=True)
        audio_length = audio_data.shape[-1]
        noise_length = noise.shape[-1]
        if noise_length > audio_length:
            offset = random.randint(0, noise_length-audio_length)
            noise = noise[..., offset:offset+audio_length]
        elif noise_length < audio_length:
            noise = torch.cat([noise, torch.zeros((noise.shape[0], audio_length-noise_length))], dim=-1)

        snr_db = random.randint(self.min_snr_db, self.max_snr_db)
        snr = math.exp(snr_db / 10)
        audio_power = audio_data.norm(p=2)
        noise_power = noise.norm(p=2)
        scale = snr * noise_power / audio_power

        return (scale * audio_data + noise ) / 2

In [12]:
#noise transformer using musan dataset
noise_transform = RandomBackgroundNoise(sampling_rate, './data/musan/noise')
noise_transformed_audio = noise_transform(audio_data)
noise_transformed_audio


tensor([[ 0.4737,  0.4771,  0.4768,  ..., -0.3347, -0.3579, -0.3763]])

In [15]:
def pad_or_truncate(x, audio_length):
    """Pad all audio to specific length."""
    length = len(x)
    if length <= audio_length:
        return np.concatenate((x, np.zeros(audio_length - length)), axis=0), length
    else:
        return x[:audio_length], audio_length


sampling_rate = 32000
audio_duration = 30
max_audio_length = audio_duration * sampling_rate # 30 * 32000
dataset='Clotho'

a, b = pad_or_truncate(noise_transformed_audio, max_audio_length)

ValueError: all the input arrays must have same number of dimensions, but the array at index 0 has 2 dimension(s) and the array at index 1 has 1 dimension(s)

In [16]:
class ComposeTransform:
    def __init__(self, transforms):
        self.transforms = transforms

    def __call__(self, audio_data):
        for t in self.transforms:
            audio_data = t(audio_data)
        return audio_data

compose_transform = ComposeTransform([
    RandomClip(sample_rate=sampling_rate, clip_length=64000),
    RandomSpeedChange(sampling_rate),
    RandomBackgroundNoise(sampling_rate, './data/musan/noise')])

In [17]:
transformed_audio = compose_transform(audio_data)
transformed_audio

tensor([[ 0.0749,  0.0877,  0.0724,  ..., -0.0111, -0.0101, -0.0087]])

In [18]:
transformed_audio.shape

torch.Size([1, 1239622])

In [19]:
transformed_audio.numpy()[0]

array([ 0.07488032,  0.08765852,  0.07237548, ..., -0.0110869 ,
       -0.01013536, -0.00868475], dtype=float32)

In [36]:
display(audio_data.shape)
display(transformed_audio.shape)

torch.Size([1, 1261260])

torch.Size([1, 1115660])

In [33]:
import IPython.display as ipd
ipd.Audio(audio_data.numpy(), rate=32000)

In [34]:
ipd.Audio(transformed_audio.numpy(), rate=32000)

꽹과리 소리 실화? 


어느정도로 늘릴건지 생각하기